# Using rapidfuzz to extract affiliations from AER
AER uses a different approach to that of JPE, QJE and RES as the data structure of AER is different. Instead of using consolidation AER uses fuzzy as the main method of extracting data

First the JSON output file from tezseract is read in and made into a useable dataframe

In [4]:
#Importing the libraries
import json
import pandas as pd
from rapidfuzz import process
import requests

# Load input files from github
tesseract_input = requests.get('https://raw.githubusercontent.com/Matt970204/Affiliations_V2/Clean-online-hosted/1.%20Input%20Data/Tesseract%20affiliation%20output/AER/AER_aff_output_1971_2010.json')
json_data = tesseract_input.json()
# Import JSON file
#f = open('/Users/MattJohnson/Desktop/Affiliations/1_Input files and processing input files/1_1_Input files/Tesseract affiliation output/AER/AER_aff_output_1971_2010.json')
#json_data = json.load(f)

# Define Journal and Dataframe
Journal_Name = 'AER'
Reference_Data_List = []

# Extract Json Data into dataframe
for key1, value1 in json_data.items():
    Article_ID = key1
    content_type = value1["content_type"]
    author_list = value1["authors"]
    authorsNo = len(author_list)
    stable_url = value1["stable_url"]
    for key2 in value1["affiliations"]:
        Ref_type = key2
        if key2 == "found":
            ref_string = value1["affiliations"][key2]
        else: 
            for key3 in value1["affiliations"]["raw"]:
                if len(value1["affiliations"]["raw"]) > 1:
                    print(key1, "   ",len(value1["affiliations"]["raw"]))
                if key3 == "1":
                    print(key3)
                    ref_string = value1["affiliations"][key2][key3]
                    print(ref_string)

    Reference_Data_List.append({'Journal_Name' : Journal_Name,
    'Authors_count' : authorsNo, 
    'Authors_list' : author_list,
    'Article_ID' : Article_ID, 'content_type' : content_type,
    'stable_url' : stable_url, 
    'Ref_type': Ref_type,  'ref_string':ref_string })

AER_aff_ref_output_1971_1999 = pd.DataFrame.from_records(Reference_Data_List)

1
['This content downloaded from\n137.158.158.62 on Wed, 19 Jan 2022 11:32:32 UTC\nA]l use subject to https://about.jstor.org/terms\n', '', 'PETER KENYON, University of Virginia:\nMy comments on Lorie Tarshis\' paper are\nfew. First, Tarshis is to be thanked for his\nreminder that "normal cost" pricing is quite\ncompatible with profit maximization and\nstandard micro theory. It is timely for\nTarshis to remind Post-Keynesians of the\nimportance of the M/4A ratio to the func-\ntional distribution of income at the micro\nlevel—that is, at the level of costs, markups,\nand prices. (Recall that Sidney Weintraub\nmade exactly the same point over twenty\nyears ago when discussing Kaldor\'s //Y\ntheory of profit share.)\n\nSecondly, Post-Keynesians would take\nissue with Tarshi! comments concerning\nthe investment funds theory of the markup.\nIn Keynesian and Post-Keynesian models,\none must be very careful about assumptions\nas to the state of long-term and short-term\nexpectations and their

In [3]:
#Read in the master sheet
#Local store of AER_master
AER_master = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/Clean-online-hosted/1.%20Input%20Data/Processed/AER_processed.xlsx")
#AER_master = pd.read_excel('/Users/MattJohnson/Desktop/Affiliations/1_Input files and processing input files/1_1_Input files/Master lists/Processed/AER_processed.xlsx')
for i in range(len(AER_master)):
    AER_master.loc[i,['Article_ID']] = AER_master.loc[i,['stable_url']].to_string().rsplit('/',1)[-1]

AER_master_condenced  = AER_master[['Article_ID','year','authors','content_type']]
AER_master_condenced['year'] = AER_master_condenced['year'].astype('int')
AER_master_condenced['Article_ID'] = AER_master_condenced['Article_ID'].astype('int')
AER_master_condenced.rename(columns = {'year':'year_master', 'content_type':'content_type_master'}, inplace = True)

# This section limites it to the years in question as well as only articles
list = []
for i in range(1971,2000):
    list.append(i)
print(list)
#mask_year = RES_master_condenced['year_master'].isin([2016,2015,2014,2013,2012,2011])
mask_year = AER_master_condenced['year_master'].isin(list)
AER_master_condenced = AER_master_condenced[mask_year]
#mask_type = RES_master_condenced['content_type_master'].isin(['Rejoiner','MISC','Review'])
#RES_master_condenced = RES_master_condenced[~mask_type]
mask_type = AER_master_condenced['content_type_master'].isin(['Article'])
AER_master_condenced = AER_master_condenced[mask_type]
#RES_master_condenced.drop(~RES_master_condenced.loc[RES_master_condenced['year_master'].isin([2016])].index, inplace=True)
print(AER_master_condenced.shape)
AER_master_condenced.head()

[1971, 1972, 1973, 1974, 1975, 1976, 1977, 1978, 1979, 1980, 1981, 1982, 1983, 1984, 1985, 1986, 1987, 1988, 1989, 1990, 1991, 1992, 1993, 1994, 1995, 1996, 1997, 1998, 1999]
(4595, 4)


/var/folders/23/ft9qf9c11rj_vqhbjml910f40000gn/T/ipykernel_3604/1422898660.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  AER_master_condenced['year'] = AER_master_condenced['year'].astype('int')
/var/folders/23/ft9qf9c11rj_vqhbjml910f40000gn/T/ipykernel_3604/1422898660.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  AER_master_condenced['Article_ID'] = AER_master_condenced['Article_ID'].astype('int')
/var/folders/23/ft9qf9c11rj_vqhbjml910f40000gn/T/ipykernel_3604/1422898660.py:11: SettingWithCopy

Article_ID  year_master                                         authors  \
4475      117047         1999                            David Lucking-Reiley   
4476      117048         1999                Jeffrey Milyo and Joel Waldfogel   
4477      117049         1999              Igal Hendel and Alessandro Lizzeri   
4478      117050         1999                                 Devashish Mitra   
4479      117051         1999  Pinelopi Koujianou Goldberg and Giovanni Maggi   

     content_type_master  
4475             Article  
4476             Article  
4477             Article  
4478             Article  
4479             Article

In [5]:
# Merging the masterfile onto the tesseract data
AER_aff_ref_output_1971_1999['Article_ID'] = AER_aff_ref_output_1971_1999['Article_ID'].astype('int')
consolidated_master_merged = AER_master_condenced.merge(AER_aff_ref_output_1971_1999, how = 'left', on = 'Article_ID')
consolidated_master_merged = consolidated_master_merged.sort_values(by=['year_master'])
consolidated_master_merged = consolidated_master_merged.reset_index(drop = True)
print(consolidated_master_merged.shape)

# The next line would be uncommented if the number of authors is wanted to be selected
#mask_auth_count = consolidated_master_merged['Authors_count'].isin([2,3,4,5,6,7])
##consolidated_master_merged = consolidated_master_merged[mask_auth_count]
consolidated_master_merged = consolidated_master_merged.reset_index(drop = True)
print(consolidated_master_merged.shape)

(4595, 11)
(4595, 11)


Next some very basic cleaning is done on the affiliation strings

In [6]:
testdata = consolidated_master_merged
testdata['ref_string'] = testdata['ref_string'].astype('str')


for i in range(len(testdata)):
    print(i)
    if testdata.iloc[i]['Ref_type'] == "raw":
        testdata.loc[i,['ref_string_clean1']] =  " ".join(testdata.iloc[i]['ref_string'])
        #x = " ".join(testdata.iloc[i]['ref_string'])
        #print(x)
        testdata.loc[i,['ref_string_clean1']] = testdata.iloc[i]['ref_string_clean1'].strip().title()
    else:
        testdata.loc[i,['ref_string_clean1']] = testdata.iloc[i]['ref_string'].strip().title()

print(testdata.columns.values)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [8]:
# Creating a dictionary for consolidation
# Read in from Excel sheet, 2 columns first one with incorrect spelling and second one with correct spellig

cities = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/Clean-online-hosted/1.%20Input%20Data/Consolidated%20Affiliations/Consolidated%20Affiliations.xlsx", 'Cities')
#cities = pd.read_excel('/Users/MattJohnson/Library/CloudStorage/OneDrive-UniversityofCapeTown/Masters_thesis/Data checks/consolidated list Final Use.xlsx', 'Cities')
cities = cities[['Incorrect spelling', 'Correct spelling']]
#print(cities.shape)

comma_in_name = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/Clean-online-hosted/1.%20Input%20Data/Consolidated%20Affiliations/Consolidated%20Affiliations.xlsx", 'Comma in name')
#comma_in_name = pd.read_excel('/Users/MattJohnson/Library/CloudStorage/OneDrive-UniversityofCapeTown/Masters_thesis/Data checks/consolidated list Final Use.xlsx', 'Comma in name')
comma_in_name = comma_in_name[['Incorrect spelling', 'Correct spelling']]
#print(comma_in_name.shape)

misspellings = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/Clean-online-hosted/1.%20Input%20Data/Consolidated%20Affiliations/Consolidated%20Affiliations.xlsx", 'Misspellings')
#misspellings = pd.read_excel('/Users/MattJohnson/Library/CloudStorage/OneDrive-UniversityofCapeTown/Masters_thesis/Data checks/consolidated list Final Use.xlsx', 'Misspellings')
misspellings = misspellings[['Incorrect spelling', 'Correct spelling']]

colleges = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/Clean-online-hosted/1.%20Input%20Data/Consolidated%20Affiliations/Consolidated%20Affiliations.xlsx", 'Colleges')
#colleges = pd.read_excel('/Users/MattJohnson/Library/CloudStorage/OneDrive-UniversityofCapeTown/Masters_thesis/Data checks/consolidated list Final Use.xlsx', 'Colleges')
colleges = colleges[['Incorrect spelling', 'Correct spelling']]

colleges_full = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/Clean-online-hosted/1.%20Input%20Data/Consolidated%20Affiliations/Consolidated%20Affiliations.xlsx", 'Colleges Full')
#colleges_full = pd.read_excel('/Users/MattJohnson/Library/CloudStorage/OneDrive-UniversityofCapeTown/Masters_thesis/Data checks/consolidated list Final Use.xlsx', 'Colleges Full')
colleges_full = colleges_full[['Incorrect spelling', 'Correct spelling']]

correct = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/Clean-online-hosted/1.%20Input%20Data/Consolidated%20Affiliations/Consolidated%20Affiliations.xlsx", 'Correct')
#correct = pd.read_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/2_Fuzzy matching/University list/consolidated list.xlsx', 'Correct')
correct = correct[['Incorrect spelling', 'Correct spelling']]

frames = [cities, misspellings, comma_in_name,colleges_full ,colleges,correct]
consolidated_affiliations = pd.concat(frames)
print(consolidated_affiliations.shape)

for i in range(len(consolidated_affiliations)):
    #Replaceing title case and stripping leading space
    #affs.iat[i,0] = affs.iat[i,0].strip().title()
    consolidated_affiliations.iloc[i]['Incorrect spelling'] = consolidated_affiliations.iloc[i]['Incorrect spelling'].strip().title()
    #affs.iat[i,0] = affs.iat[i,0].strip().upper()

consolidated_affiliations_dict = consolidated_affiliations.set_index('Incorrect spelling').to_dict()['Correct spelling']
print(consolidated_affiliations_dict)

(1714, 2)
{'Ames, Iowa': 'Ames Iowa United States (City)', 'Ames, Iowa, Usa': 'Ames Iowa United States (City)', 'Antwerp': 'Antwerp Belguim (City)', 'Auckland, New Zealand': 'Auckland New Zealand (City)', 'Auckland, Nz': 'Auckland New Zealand (City)', 'Baghdad': 'Baghdad Iraq (City)', 'Baltimore': 'Baltimore Maryland (City)', 'Baltimore, Usa Kzlvin J Lancaster': 'Baltimore Maryland (City)', 'Belfast': 'Belfast Ireland (City)', 'Berkeley': 'Berkeley California United States (City)', 'Berkeley, California': 'Berkeley California United States (City)', 'Birmingham': 'Birmingham United Kingdom (City)', 'Birmingham And Ames, Iowa': 'Birmingham United Kingdom (City)', 'Bloomington, Indiana': 'Bloomington Indiana United States (City)', 'Bristol': 'Bristol United Kingdom (City)', 'Brooklyn, New York': 'Brooklyn New York United States (City)', 'Brunswick, Maine Davidp Braybrooke': 'Brunswick Maine United States (City)', 'Brussels': 'Brussels Belgium (City)', 'Brussels, Belgium': 'Brussels Belgiu

In [9]:
# Load in the list of unique Universites from github stored in 2_fuzzy matching
affs = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/Clean-online-hosted/1.%20Input%20Data/Consolidated%20Affiliations/Consolidated%20Affiliations.xlsx", 'Fuzzy match')
#affs = pd.read_excel('/Users/MattJohnson/Library/CloudStorage/OneDrive-UniversityofCapeTown/Masters_thesis/Data checks/consolidated list 09 11.xlsx', 'Fuzzy match')
print(affs.shape)
print(affs.head())
affs = affs[['Affilliation']]


for i in range(len(affs)):
    #Replaceing title case and stripping leading space
    #affs.iat[i,0] = affs.iat[i,0].strip().title()
    affs.iloc[i]['Affilliation'] = affs.iloc[i]['Affilliation'].strip().title()
    #affs.iat[i,0] = affs.iat[i,0].strip().upper()

Affiliation_choices = affs['Affilliation'].values.tolist()

print(affs['Affilliation'].tail())

(828, 1)
                   Affilliation
0           Aberdeen University
1  Abilene Christian University
2               Academia Sinica
3             Acadia University
4   African School Of Economics
823        State University Of New York At Buffalo
824    State University Of New York At Stony Brook
825       State University Of New York At Westbury
826                University Of Wisconsin-Madison
827              University Of Wisconsin-Milwaukee
Name: Affilliation, dtype: object


In [10]:
# Add in the know columns of end data, this is a hindsight addition to the code and should have been there from the start
testdata["0_Auth_string_found"] = ""
testdata["0_Auth_affs_0"] = ""
testdata["0_Auth_affs_1"] = ""
testdata["0_Auth_affs_2"] = ""
testdata["0_Auth_affs_3"] = ""
testdata["0_Auth_affs_4"] = ""

testdata["1_Auth_string_found"] = ""
testdata["1_Auth_affs_0"] = ""
testdata["1_Auth_affs_1"] = ""
testdata["1_Auth_affs_2"] = ""
testdata["1_Auth_affs_3"] = ""
testdata["1_Auth_affs_4"] = ""

testdata["2_Auth_string_found"] = ""
testdata["2_Auth_affs_0"] = ""
testdata["2_Auth_affs_1"] = ""
testdata["2_Auth_affs_2"] = ""
testdata["2_Auth_affs_3"] = ""
testdata["2_Auth_affs_4"] = ""

testdata["3_Auth_string_found"] = ""
testdata["3_Auth_affs_0"] = ""
testdata["3_Auth_affs_1"] = ""
testdata["3_Auth_affs_2"] = ""
testdata["3_Auth_affs_3"] = ""
testdata["3_Auth_affs_4"] = ""

testdata["4_Auth_affs_0"] = ""
testdata["4_Auth_affs_1"] = ""
testdata["4_Auth_affs_2"] = ""
testdata["4_Auth_affs_3"] = ""

testdata["5_Auth_affs_0"] = ""
testdata["6_Auth_affs_0"] = ""
testdata["7_Auth_affs_0"] = ""

In [13]:
import re
from rapidfuzz import fuzz
import math


#for x in range(len(testdata)):
start = 1
end = 2
#for x in range(start,end):

for x in range(len(testdata)):
    ref_string = testdata.iloc[x]['ref_string_clean1']
    
## Removing the Discussants
    discussants_ratio = fuzz.partial_ratio(ref_string, "* Discussants")
    print(discussants_ratio)
    if discussants_ratio > 95:
        ref_string_discussants = re.split(r"\n\n" , ref_string)
        ref_string = ref_string_discussants[1]

    #ref_string = re.sub(r'-','',ref_string).title().strip()
    ref_string = re.sub(r'\-\n','',ref_string).title().strip()
    ref_string = re.sub(r'\n',' ',ref_string).title().strip()
    affiliations = []
    authors_count = testdata.iloc[x]['Authors_count'].astype('int')
    print(authors_count)

    #For 1 author
    if authors_count == 1:
        ref_string_email = re.split(r"Email" , ref_string)
        if len(ref_string_email[0]) < 10:
            ref_string_email_0 = ref_string
        else:
            ref_string_email_0 = ref_string_email[0]

        print(ref_string_email_0)
        for z in Affiliation_choices:
            if pd.notnull(ref_string):
                # z is the affilition choice being matched
                # author_aff is the input string based on authors
                    ratio  = fuzz.partial_ratio(ref_string_email_0, z)
                    if ratio > 93:
                        #Appending the affiliation and the ratio to affiliations list
                        affiliations.append(z)
                                #Errors
                        if len(affiliations) == 8:
                            break
        print(affiliations)
        for e in range(len(affiliations)):
            print(affiliations[e])
            #testdata.loc[x, '0_Auth_affs'] = affiliations[e]
            testdata.loc[x, '0_Auth_affs_'+str(e)] = affiliations[e]
            #testdata.loc['0_Auth_aff_ratio'+str(e)] = affiliations[e][1]
            #print(affiliations[e][0])
            #print(testdata.loc[x, '0_Auth_affs_'+str(e)])
            #print(affiliations[e][1])
            #print(testdata.loc[x,'Auth_'+str(i)+'_'+ str(e)+'_aff'])

    if authors_count == 2:
        
        authors = testdata.iloc[x]['Authors_list']
        
        for m in range(len(authors)):
            authors[m] = authors[m].title().strip()
            auth_split = re.split(r" " , authors[m]) 
            print(auth_split)
            auth_surname = auth_split[-1]
            print(auth_surname)


            auth_1_ratio  = fuzz.partial_ratio(ref_string, auth_surname)
            respectively_ratio  = fuzz.partial_ratio(ref_string, "Respectively")

            # Found author surname

            if respectively_ratio > 92:
                testdata.loc[x, 'Split method'] = "Respectively"
                print("Respectively")
                ref_string_respectively = re.split(r"Respectively\." , ref_string)[0]
                print("REF STRING:::", ref_string_respectively)

                semi_colon_ratio = respectively_ratio  = fuzz.partial_ratio(ref_string_respectively, ";")
                and_ratio = respectively_ratio  = fuzz.partial_ratio(ref_string_respectively, "And")

                if semi_colon_ratio > 92:
                    auth_0_aff = re.split(r";" , ref_string_respectively)[0]
                    testdata.loc[x, '0_Auth_string_found'] = auth_0_aff
                    auth_1_aff = re.split(r";" , ref_string_respectively)[1]
                    testdata.loc[x, '1_Auth_string_found'] = auth_1_aff

                elif and_ratio > 92:
                    auth_0_aff = re.split(r"And" , ref_string_respectively)[0]
                    testdata.loc[x, '0_Auth_string_found'] = auth_0_aff
                    auth_1_aff = re.split(r"And" , ref_string_respectively)[1]
                    testdata.loc[x, '1_Auth_string_found'] = auth_1_aff

                else:
                    auth_0_aff = ref_string_respectively
                    testdata.loc[x, '0_Auth_string_found'] = ""
                    auth_1_aff = ref_string_respectively
                    testdata.loc[x, '1_Auth_string_found'] = ""

                # A1
                affiliations = []       
                for z in Affiliation_choices:
                    ratio  = fuzz.partial_ratio(auth_0_aff, z)
                    if ratio > 92:
                        print(ratio)
                        affiliations.append(z)
                                #Errors
                        if len(affiliations) == 8:
                            break
                print(affiliations)

                for affs in range(len(affiliations)):
                    testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]

                # A2
                affiliations = []
                for z in Affiliation_choices:
                    ratio  = fuzz.partial_ratio(auth_1_aff, z)
                    if ratio > 92:
                        print(ratio)
                        affiliations.append(z)
                                #Errors
                        if len(affiliations) == 8:
                            break
                print(affiliations)

                for affs in range(len(affiliations)):
                    testdata.loc[x, '1_Auth_affs_'+ str(affs)] = affiliations[affs]
            
            elif auth_1_ratio > 92:
                testdata.loc[x, 'Split method'] = "Author Surname"
                try:

                    auth_1_aff = re.split(r"\;" , ref_string)[0]
                    auth_2_aff_full = re.split(r"\;" , ref_string)[1]
                    print(auth_2_aff_full)

                    auth_2_aff = re.split(r"\." , auth_2_aff_full)[0]

                    auth_1_ratio  = fuzz.partial_ratio(auth_1_aff, auth_surname)
                    if auth_1_ratio > 92:
                        print("found 1")
                        testdata.loc[x, '0_Auth_string_found'] = auth_1_aff
                        auth_1_aff_confirmed = auth_1_aff
                    
                    print(auth_2_aff)
                    auth_2_ratio  = fuzz.partial_ratio(auth_2_aff, auth_surname)
                    if auth_2_ratio > 92:
                        print("found 2")
                        testdata.loc[x, '1_Auth_string_found'] = auth_2_aff
                        auth_2_aff_confirmed = auth_2_aff

            # A1
                    affiliations = []       
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_1_aff_confirmed, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]

            # A2
                    affiliations = []
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_2_aff_confirmed, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '1_Auth_affs_'+ str(affs)] = affiliations[affs]

                except :
                    print("Failed")
                    affiliations = []       
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(ref_string, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]
                        testdata.loc[x, '1_Auth_affs_'+str(affs)] = affiliations[affs]
            
             #Author name not found
            

            else:
                testdata.loc[x, 'Split method'] = "No split"
                affiliations = []       
                for z in Affiliation_choices:
                    ratio  = fuzz.partial_ratio(ref_string, z)
                    if ratio > 92:
                        print(ratio)
                        affiliations.append(z)
                                #Errors
                        if len(affiliations) == 8:
                            break
                print(affiliations)

                for affs in range(len(affiliations)):
                    testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]
                    testdata.loc[x, '1_Auth_affs_'+str(affs)] = affiliations[affs]

       


    if authors_count == 3:
        
        authors = testdata.iloc[x]['Authors_list']
        
        for m in range(len(authors)):
            authors[m] = authors[m].title().strip()
            auth_split = re.split(r" " , authors[m]) 
            print(auth_split)
            auth_surname = auth_split[-1]
            print(auth_surname)


            auth_1_ratio  = fuzz.partial_ratio(ref_string, auth_surname)

            
            respectively_ratio  = fuzz.partial_ratio(ref_string, "Respectively")

            ref_string_first_30 = ref_string[0:30]
            semi_colon_ratio = respectively_ratio  = fuzz.partial_ratio(ref_string_first_30, ";")

            # Found author surname
            if respectively_ratio > 92 or semi_colon_ratio > 92:
                try:
                
                    testdata.loc[x, 'Split method'] = "Respectively"
                    print("Respectively")
                    ref_string_respectively = re.split(r"Respectively\." , ref_string)[0]
                    print("REF STRING:::", ref_string_respectively)

                    semi_colon_ratio = respectively_ratio  = fuzz.partial_ratio(ref_string_respectively, ";")
                    and_ratio = respectively_ratio  = fuzz.partial_ratio(ref_string_respectively, "And")

                    if semi_colon_ratio > 92:
                        auth_0_aff = re.split(r";" , ref_string_respectively)[0]
                        testdata.loc[x, '0_Auth_string_found'] = auth_0_aff
                        auth_1_aff = re.split(r";" , ref_string_respectively)[1]
                        testdata.loc[x, '1_Auth_string_found'] = auth_1_aff
                        auth_2_aff = re.split(r";" , ref_string_respectively)[2]
                        testdata.loc[x, '2_Auth_string_found'] = auth_2_aff

                    elif and_ratio > 92:
                        auth_0_aff = re.split(r"And" , ref_string_respectively)[0]
                        testdata.loc[x, '0_Auth_string_found'] = auth_0_aff
                        auth_1_aff = re.split(r"And" , ref_string_respectively)[1]
                        testdata.loc[x, '1_Auth_string_found'] = auth_1_aff
                        auth_2_aff = re.split(r"And" , ref_string_respectively)[2]
                        testdata.loc[x, '2_Auth_string_found'] = auth_2_aff

                    else:
                        auth_0_aff = ref_string_respectively
                        testdata.loc[x, '0_Auth_string_found'] = ""
                        auth_1_aff = ref_string_respectively
                        testdata.loc[x, '1_Auth_string_found'] = ""
                        auth_2_aff = ref_string_respectively
                        testdata.loc[x, '2_Auth_string_found'] = ""

                    # A1
                    affiliations = []       
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_0_aff, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]

                    # A2
                    affiliations = []
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_1_aff, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '1_Auth_affs_'+ str(affs)] = affiliations[affs]
                    
                    # A3
                    affiliations = []
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_2_aff, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '2_Auth_affs_'+ str(affs)] = affiliations[affs]
                except: 
                        testdata.loc[x, '0_Auth_affs_'+str(affs)] = ""
                        testdata.loc[x, '1_Auth_affs_'+str(affs)] = ""
                        testdata.loc[x, '2_Auth_affs_'+str(affs)] = ""
            
            elif auth_1_ratio > 92:
                testdata.loc[x, 'Split method'] = "Author Surname"
                try:


                    auth_0_aff = re.split(r";" , ref_string)[0]
                    testdata.loc[x, '0_Auth_string_found'] = auth_0_aff
                    auth_1_aff = re.split(r";" , ref_string)[1]
                    testdata.loc[x, '1_Auth_string_found'] = auth_1_aff
                    auth_2_aff = re.split(r";" , ref_string)[2]
                    testdata.loc[x, '2_Auth_string_found'] = auth_2_aff


                    auth_0_ratio  = fuzz.partial_ratio(auth_0_aff, auth_surname)
                    if auth_0_ratio > 92:
                        print("found 0")
                        testdata.loc[x, '0_Auth_string_found'] = auth_0_aff
                        auth_0_aff_confirmed = auth_0_aff

                    print(auth_1_aff)
                    auth_1_ratio  = fuzz.partial_ratio(auth_1_aff, auth_surname)
                    if auth_1_ratio > 92:
                        print("found 1")
                        testdata.loc[x, '1_Auth_string_found'] = auth_1_aff
                        auth_1_aff_confirmed = auth_1_aff
                    
                    print(auth_2_aff)
                    auth_2_ratio  = fuzz.partial_ratio(auth_2_aff, auth_surname)
                    if auth_2_ratio > 92:
                        print("found 2")
                        testdata.loc[x, '1_Auth_string_found'] = auth_2_aff
                        auth_2_aff_confirmed = auth_2_aff

            # A1
                    affiliations = []       
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_0_aff_confirmed, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]

            # A2
                    affiliations = []
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_1_aff_confirmed, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '1_Auth_affs_'+ str(affs)] = affiliations[affs]
               
                # A3
                    affiliations = []
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_2_aff_confirmed, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '2_Auth_affs_'+ str(affs)] = affiliations[affs]

                except :
                    print("Failed")
                    affiliations = []       
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(ref_string, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]
                        testdata.loc[x, '1_Auth_affs_'+str(affs)] = affiliations[affs]
                        testdata.loc[x, '2_Auth_affs_'+str(affs)] = affiliations[affs]
            
             #Author name not found
            

            else:
                testdata.loc[x, 'Split method'] = "No split"
                affiliations = []       
                for z in Affiliation_choices:
                    ratio  = fuzz.partial_ratio(ref_string, z)
                    if ratio > 92:
                        print(ratio)
                        affiliations.append(z)
                                #Errors
                        if len(affiliations) == 8:
                            break
                print(affiliations)

                for affs in range(len(affiliations)):
                    testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]
                    testdata.loc[x, '1_Auth_affs_'+str(affs)] = affiliations[affs]
                    testdata.loc[x, '2_Auth_affs_'+str(affs)] = affiliations[affs]

       
    if authors_count == 4:
        
        authors = testdata.iloc[x]['Authors_list']
        
        for m in range(len(authors)):
            authors[m] = authors[m].title().strip()
            auth_split = re.split(r" " , authors[m]) 
            print(auth_split)
            auth_surname = auth_split[-1]
            print(auth_surname)


            auth_1_ratio  = fuzz.partial_ratio(ref_string, auth_surname)
            respectively_ratio  = fuzz.partial_ratio(ref_string, "Respectively")
            semi_colon_ratio = respectively_ratio  = fuzz.partial_ratio(ref_string, ";")

            # Found author surname

            if respectively_ratio > 92 or semi_colon_ratio > 92:
                try:
                    testdata.loc[x, 'Split method'] = "Respectively"
                    print("Respectively")
                    ref_string_respectively = re.split(r"Respectively\." , ref_string)[0]
                    print("REF STRING:::", ref_string_respectively)

                    semi_colon_ratio = respectively_ratio  = fuzz.partial_ratio(ref_string_respectively, ";")
                    and_ratio = respectively_ratio  = fuzz.partial_ratio(ref_string_respectively, "And")

                    if semi_colon_ratio > 92:
                        auth_0_aff = re.split(r";" , ref_string_respectively)[0]
                        testdata.loc[x, '0_Auth_string_found'] = auth_0_aff
                        auth_1_aff = re.split(r";" , ref_string_respectively)[1]
                        testdata.loc[x, '1_Auth_string_found'] = auth_1_aff
                        auth_2_aff = re.split(r";" , ref_string_respectively)[2]
                        testdata.loc[x, '2_Auth_string_found'] = auth_2_aff
                        auth_3_aff = re.split(r";" , ref_string_respectively)[2]
                        testdata.loc[x, '3_Auth_string_found'] = auth_3_aff

                    elif and_ratio > 92:
                        auth_0_aff = re.split(r"And" , ref_string_respectively)[0]
                        testdata.loc[x, '0_Auth_string_found'] = auth_0_aff
                        auth_1_aff = re.split(r"And" , ref_string_respectively)[1]
                        testdata.loc[x, '1_Auth_string_found'] = auth_1_aff
                        auth_2_aff = re.split(r"And" , ref_string_respectively)[2]
                        testdata.loc[x, '2_Auth_string_found'] = auth_2_aff
                        auth_3_aff = re.split(r"And" , ref_string_respectively)[2]
                        testdata.loc[x, '3_Auth_string_found'] = auth_3_aff

                    else:
                        auth_0_aff = ref_string_respectively
                        testdata.loc[x, '0_Auth_string_found'] = ""
                        auth_1_aff = ref_string_respectively
                        testdata.loc[x, '1_Auth_string_found'] = ""
                        auth_2_aff = ref_string_respectively
                        testdata.loc[x, '2_Auth_string_found'] = ""
                        auth_3_aff = ref_string_respectively
                        testdata.loc[x, '3_Auth_string_found'] = ""

                    # A1
                    affiliations = []       
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_0_aff, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]

                    # A2
                    affiliations = []
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_1_aff, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '1_Auth_affs_'+ str(affs)] = affiliations[affs]
                    
                    # A3
                    affiliations = []
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_2_aff, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '2_Auth_affs_'+ str(affs)] = affiliations[affs]

                    # A3
                    affiliations = []
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_3_aff, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '3_Auth_affs_'+ str(affs)] = affiliations[affs]
                except:
            

                        testdata.loc[x, '0_Auth_affs_'+str(affs)] = ""
                        testdata.loc[x, '1_Auth_affs_'+str(affs)] = ""
                        testdata.loc[x, '2_Auth_affs_'+str(affs)] = ""
                        testdata.loc[x, '3_Auth_affs_'+str(affs)] = ""
            elif auth_1_ratio > 92:
                testdata.loc[x, 'Split method'] = "Author Surname"
                try:


                    auth_0_aff = re.split(r";" , ref_string)[0]
                    testdata.loc[x, '0_Auth_string_found'] = auth_0_aff
                    auth_1_aff = re.split(r";" , ref_string)[1]
                    testdata.loc[x, '1_Auth_string_found'] = auth_1_aff
                    auth_2_aff = re.split(r";" , ref_string)[2]
                    testdata.loc[x, '2_Auth_string_found'] = auth_2_aff
                    auth_3_aff = re.split(r";" , ref_string)[3]
                    testdata.loc[x, '3_Auth_string_found'] = auth_3_aff


                    auth_0_ratio  = fuzz.partial_ratio(auth_0_aff, auth_surname)
                    if auth_0_ratio > 92:
                        print("found 0")
                        testdata.loc[x, '0_Auth_string_found'] = auth_0_aff
                        auth_0_aff_confirmed = auth_0_aff

                    print(auth_1_aff)
                    auth_1_ratio  = fuzz.partial_ratio(auth_1_aff, auth_surname)
                    if auth_1_ratio > 92:
                        print("found 1")
                        testdata.loc[x, '1_Auth_string_found'] = auth_1_aff
                        auth_1_aff_confirmed = auth_1_aff
                    
                    print(auth_2_aff)
                    auth_2_ratio  = fuzz.partial_ratio(auth_2_aff, auth_surname)
                    if auth_2_ratio > 92:
                        print("found 2")
                        testdata.loc[x, '2_Auth_string_found'] = auth_2_aff
                        auth_2_aff_confirmed = auth_2_aff

                    print(auth_3_aff)
                    auth_3_ratio  = fuzz.partial_ratio(auth_3_aff, auth_surname)
                    if auth_3_ratio > 92:
                        print("found 2")
                        testdata.loc[x, '3_Auth_string_found'] = auth_3_aff
                        auth_3_aff_confirmed = auth_3_aff

            # A1
                    affiliations = []       
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_0_aff_confirmed, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]

            # A2
                    affiliations = []
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_1_aff_confirmed, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '1_Auth_affs_'+ str(affs)] = affiliations[affs]
               
                # A3
                    affiliations = []
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_2_aff_confirmed, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '2_Auth_affs_'+ str(affs)] = affiliations[affs]
                # A3
                    affiliations = []
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(auth_3_aff_confirmed, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '3_Auth_affs_'+ str(affs)] = affiliations[affs]

                except :
                    print("Failed")
                    affiliations = []       
                    for z in Affiliation_choices:
                        ratio  = fuzz.partial_ratio(ref_string, z)
                        if ratio > 92:
                            print(ratio)
                            affiliations.append(z)
                                    #Errors
                            if len(affiliations) == 8:
                                break
                    print(affiliations)

                    for affs in range(len(affiliations)):
                        testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]
                        testdata.loc[x, '1_Auth_affs_'+str(affs)] = affiliations[affs]
                        testdata.loc[x, '2_Auth_affs_'+str(affs)] = affiliations[affs]
                        testdata.loc[x, '3_Auth_affs_'+str(affs)] = affiliations[affs]
            
             #Author name not found
            

            else:
                testdata.loc[x, 'Split method'] = "No split"
                affiliations = []       
                for z in Affiliation_choices:
                    ratio  = fuzz.partial_ratio(ref_string, z)
                    if ratio > 92:
                        print(ratio)
                        affiliations.append(z)
                                #Errors
                        if len(affiliations) == 8:
                            break
                print(affiliations)

                for affs in range(len(affiliations)):
                    testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]
                    testdata.loc[x, '1_Auth_affs_'+str(affs)] = affiliations[affs]
                    testdata.loc[x, '2_Auth_affs_'+str(affs)] = affiliations[affs]
                    testdata.loc[x, '3_Auth_affs_'+str(affs)] = affiliations[affs]

    if authors_count > 4:
        affiliations = []       
        for z in Affiliation_choices:
            ratio  = fuzz.partial_ratio(ref_string, z)
            if ratio > 92:
                print(ratio)
                affiliations.append(z)
                        #Errors
                if len(affiliations) == 8:
                    break
        print(affiliations)

        for affs in range(len(affiliations)):
            testdata.loc[x, '0_Auth_affs_'+str(affs)] = affiliations[affs]
            testdata.loc[x, '1_Auth_affs_'+str(affs)] = affiliations[affs]
            testdata.loc[x, '2_Auth_affs_'+str(affs)] = affiliations[affs]
            testdata.loc[x, '3_Auth_affs_'+str(affs)] = affiliations[affs]
            testdata.loc[x, '4_Auth_affs_'+str(affs)] = affiliations[affs]
    print("Number",x)
testdata.iloc[[start]].head()    

23.076923076923073
1
[ ' T H I S   C O N T E N T   D O W N L O A D E D   F R O M   1 6 5 . 9 5 . 2 2 6 . 1 0 0   O N   M O N ,   0 2   N O V   2 0 1 5   0 5 : 5 7 : 0 7   U T C \ N A I I   U S E   S U B J E C T   T O   J S T O R   T E R M S   A N D   C O N D I T I O N S \ N \ N ' ,   ' C O N S E Q U E N T L Y ,   M A X I M I Z I N G   T 1 ( 7 )   B Y   T A K I N G \ N T H E   P A R T I A L   D E R I V A T I V E   O F I ( 7 ) / 8 9 S U ( R )   A N D \ N S E T T I N G   I T   E Q U A L   T O   Z E R O   A L S O   M A K E S   T H E   P A R T I A L \ N D E R I V A T I V E   À Y I ( 7 ) / 0   S U ( 7 )   Z E R O . \ N \ N T H U S   A L L   S O L U T I O N S   O F   M Y   M O D E L   H O L D \ N W H E T H E R   O R   N O T   E N T R E P R E N E U R S   I G N O R E   T H E I R \ N O W N   I N F L U E N C E   U P O N   N A T I O N A L   M O N E Y   I N C O M E \ N A N D   S A V I N G S . \ N ' ,   ' ' ,   ' ' ,   ' ' ,   ' ' ,   ' ' ,   ' ' ,   ' ' ,   ' ' ,   ' O F I ( 7 ) \ N 9 Y I ( R )   -

Article_ID  year_master             authors content_type_master  \
1     1811859         1971  Thomas C. Lowinger             Article   

  Journal_Name  Authors_count          Authors_list content_type  \
1          AER              1  [Thomas C. Lowinger]      Article   

                             stable_url Ref_type  ... 1_Auth_affs_6  \
1  https://www.jstor.org/stable/1811859    found  ...           NaN   

  1_Auth_affs_7 0_Auth_affs_6 0_Auth_affs_7 2_Auth_affs_6 2_Auth_affs_7  \
1           NaN           NaN           NaN           NaN           NaN   

  3_Auth_affs_6 3_Auth_affs_7 4_Auth_affs_6 4_Auth_affs_7  
1           NaN           NaN           NaN           NaN  

[1 rows x 60 columns]

In [14]:
# Creating a dictionary for consolidation
# Read in from Excel sheet, 2 columns first one with incorrect spelling and second one with correct spellig
import pandas as pd

Corrections = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/Clean-online-hosted/1.%20Input%20Data/Consolidated%20Affiliations/Consolidated%20Affiliations.xlsx", 'Systems')
#Corrections = pd.read_excel('/Users/MattJohnson/Library/CloudStorage/OneDrive-UniversityofCapeTown/Masters_thesis/Data checks/consolidated list 09 11.xlsx', 'Sheet3')
Corrections = Corrections[['Incorrect spelling', 'Correct spelling']]

#Remove cities
frames = [Corrections]
consolidated_affiliations = pd.concat(frames)
print(consolidated_affiliations.shape)

for i in range(len(consolidated_affiliations)):
    #Replaceing title case and stripping leading space
    #affs.iat[i,0] = affs.iat[i,0].strip().title()
    consolidated_affiliations.iloc[i]['Incorrect spelling'] = consolidated_affiliations.iloc[i]['Incorrect spelling'].strip().title()
    #affs.iat[i,0] = affs.iat[i,0].strip().upper()

consolidated_affiliations_dict = consolidated_affiliations.set_index('Incorrect spelling').to_dict()['Correct spelling']
print(consolidated_affiliations_dict)

(20, 2)
{'University Of California, Berkeley': 'UCB', 'University Of California, Davis': 'UCD', 'University Of California, Irvine': 'UCI', 'University Of California, Los Angeles': 'UCLA', 'University Of California, Merced': 'UCM', 'University Of California, Riverside': 'UCR', 'University Of California, San Diego': 'UCSD', 'University Of California, San Francisco': 'UCSF', 'University Of California, Santa Barbara': 'UCSB', 'University Of California, Santa Cruz': 'UCSC', 'State University Of New York At Albany': 'Suny At Albany', 'State University Of New York At Binghamton': 'Suny At Binghampton', 'State University Of New York At Buffalo': 'Suny At Buffalo', 'State University Of New York At Stony Brook': 'Suny At Stony Brook', 'State University Of New York At Westbury': 'Suny At Westbury', 'California State University, Fullerton': 'California State University At Fullerton', 'California State College At Fullerton': 'California State University At Fullerton', 'California State University, 

In [15]:
start = 0
end = 500

testdata["3_Auth_affs_0"] = ""
#for i in range(start,end):
for i in range(len(testdata)):
    print(i)
    for key in consolidated_affiliations_dict.keys():
        
        if pd.notnull(testdata.iloc[i]['0_Auth_affs_0']):
            if key in testdata.iloc[i]['0_Auth_affs_0']:
                testdata.loc[i,'0_Auth_affs_0']  = re.sub(key, consolidated_affiliations_dict[key],testdata.iloc[i]['0_Auth_affs_0']).strip().rstrip(',')
        
        if pd.notnull(testdata.iloc[i]['0_Auth_affs_1']):
            if key in testdata.iloc[i]['0_Auth_affs_1']:
                testdata.loc[i,'0_Auth_affs_1']  = re.sub(key, consolidated_affiliations_dict[key],testdata.iloc[i]['0_Auth_affs_1']).strip().rstrip(',')
        
        if pd.notnull(testdata.iloc[i]['0_Auth_affs_2']):
            if key in testdata.iloc[i]['0_Auth_affs_2']:
                testdata.loc[i,'0_Auth_affs_2']  = re.sub(key, consolidated_affiliations_dict[key],testdata.iloc[i]['0_Auth_affs_2']).strip().rstrip(',')
        
        if pd.notnull(testdata.iloc[i]['0_Auth_affs_3']):
            if key in testdata.iloc[i]['0_Auth_affs_3']:
                testdata.loc[i,'0_Auth_affs_3']  = re.sub(key, consolidated_affiliations_dict[key],testdata.iloc[i]['0_Auth_affs_3']).strip().rstrip(',')
        
        if pd.notnull(testdata.iloc[i]['0_Auth_affs_4']):
            if key in testdata.iloc[i]['0_Auth_affs_4']:
                testdata.loc[i,'0_Auth_affs_4']  = re.sub(key, consolidated_affiliations_dict[key],testdata.iloc[i]['0_Auth_affs_4']).strip().rstrip(',')
        
        if pd.notnull(testdata.iloc[i]['1_Auth_affs_0']):
            if key in testdata.iloc[i]['1_Auth_affs_0']:
                testdata.loc[i,'1_Auth_affs_0']  = re.sub(key, consolidated_affiliations_dict[key],testdata.iloc[i]['1_Auth_affs_0']).strip().rstrip(',')
        
        if pd.notnull(testdata.iloc[i]['2_Auth_affs_0']):
            if key in testdata.iloc[i]['2_Auth_affs_0']:
                testdata.loc[i,'2_Auth_affs_0']  = re.sub(key, consolidated_affiliations_dict[key],testdata.iloc[i]['2_Auth_affs_0']).strip().rstrip(',')
        
        if pd.notnull(testdata.iloc[i]['3_Auth_affs_0']):
            if key in testdata.iloc[i]['3_Auth_affs_0']:
                testdata.loc[i,'3_Auth_affs_0']  = re.sub(key, consolidated_affiliations_dict[key],testdata.iloc[i]['3_Auth_affs_0']).strip().rstrip(',')

testdata.iloc[[start]].head()   

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

Article_ID  year_master     authors content_type_master Journal_Name  \
0     1910574         1971  Hans Brems             Article          AER   

   Authors_count  Authors_list content_type  \
0              1  [Hans Brems]      Article   

                             stable_url Ref_type  ... 1_Auth_affs_6  \
0  https://www.jstor.org/stable/1910574      raw  ...           NaN   

  1_Auth_affs_7 0_Auth_affs_6 0_Auth_affs_7 2_Auth_affs_6 2_Auth_affs_7  \
0           NaN           NaN           NaN           NaN           NaN   

  3_Auth_affs_6 3_Auth_affs_7 4_Auth_affs_6 4_Auth_affs_7  
0           NaN           NaN           NaN           NaN  

[1 rows x 60 columns]

In [16]:
print(testdata.columns.values)

['Article_ID' 'year_master' 'authors' 'content_type_master' 'Journal_Name'
 'Authors_count' 'Authors_list' 'content_type' 'stable_url' 'Ref_type'
 'ref_string' 'ref_string_clean1' '0_Auth_string_found' '0_Auth_affs_0'
 '0_Auth_affs_1' '0_Auth_affs_2' '0_Auth_affs_3' '0_Auth_affs_4'
 '1_Auth_string_found' '1_Auth_affs_0' '1_Auth_affs_1' '1_Auth_affs_2'
 '1_Auth_affs_3' '1_Auth_affs_4' '2_Auth_string_found' '2_Auth_affs_0'
 '2_Auth_affs_1' '2_Auth_affs_2' '2_Auth_affs_3' '2_Auth_affs_4'
 '3_Auth_string_found' '3_Auth_affs_0' '3_Auth_affs_1' '3_Auth_affs_2'
 '3_Auth_affs_3' '3_Auth_affs_4' '4_Auth_affs_0' '4_Auth_affs_1'
 '4_Auth_affs_2' '4_Auth_affs_3' '5_Auth_affs_0' '6_Auth_affs_0'
 '7_Auth_affs_0' 'Split method' '4_Auth_affs_4' '0_Auth_affs_5'
 '1_Auth_affs_5' '2_Auth_affs_5' '3_Auth_affs_5' '4_Auth_affs_5'
 '1_Auth_affs_6' '1_Auth_affs_7' '0_Auth_affs_6' '0_Auth_affs_7'
 '2_Auth_affs_6' '2_Auth_affs_7' '3_Auth_affs_6' '3_Auth_affs_7'
 '4_Auth_affs_6' '4_Auth_affs_7']


In [17]:
testdata = testdata[['Journal_Name' ,'Authors_count', 'Authors_list', 'authors', 'Article_ID', 'content_type',
'stable_url', 'year_master', 'Ref_type' ,'ref_string', 'ref_string_clean1',
'0_Auth_string_found', '0_Auth_affs_0', '0_Auth_affs_1', '0_Auth_affs_2', '0_Auth_affs_3', '0_Auth_affs_4', 
'1_Auth_string_found', '1_Auth_affs_0' , '1_Auth_affs_1', '1_Auth_affs_2', '1_Auth_affs_3', '1_Auth_affs_4',
'2_Auth_string_found' ,'2_Auth_affs_0', '2_Auth_affs_1', '2_Auth_affs_2', '2_Auth_affs_3', '2_Auth_affs_4',
'3_Auth_string_found', '3_Auth_affs_0', '3_Auth_affs_1', '3_Auth_affs_2', '3_Auth_affs_3', '3_Auth_affs_4',
'4_Auth_affs_0', '4_Auth_affs_1', '4_Auth_affs_2' , '4_Auth_affs_3',
'5_Auth_affs_0','6_Auth_affs_0','7_Auth_affs_0',]]

In [ ]:
# Excel output to get an overview of the data
#testdata.head
#testdata.to_excel('/Users/MattJohnson/Desktop/Affiliations/2. Extracting affilitations from Tesseract/2.2. Fuzzy Matching/2.2.A. Data created in 2.2. AER/AER 1971-1999 first pass affiliations.xlsx') 